## EEG_MODEL_1 

In [15]:
# Данная программа будет состоять из нескольких концептуальных частей:
# 1. loading_preprocessed_data - функция, отвечающая за загрузку предобработанных данных, из заранее заготовленного датасета
# 2. feature_extraction/selection - выделяем и выбор признаков, с целью уменьшения конечной выборки данных
# 3. classification - классификация сигналов, разнесение сигналов по соответствующим им эмоциям
# 4. visualisation
# Конечная цель - рабочая система, которая будет по загруженным в неё данным определять человеческую эмоцию

In [16]:
%pip install mne
%pip install pandas

’ҐЄгй п Є®¤®ў п бва ­Ёж : 1251Note: you may need to restart the kernel to use updated packages.

’ҐЄгй п Є®¤®ў п бва ­Ёж : 1251
Note: you may need to restart the kernel to use updated packages.


In [17]:
# offline recognize emotion
# using libraries for project
import pandas as pd
import numpy as np
import os
import scipy.io as spio
import pywt

from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split, GridSearchCV

from sklearn.preprocessing import normalize
from sklearn.svm import SVC

In [18]:
directory = "C:/Users/alash/Desktop/4 курс/Diplom/program/EEG-Offline-Recognize-Emotions/datasets/"
path_for_file = "C:/Users/alash/Desktop/4 курс/Diplom/program/datasets/SEED_Multimodal/SEED_Multimodal/Chinese/01" \
                "-EEG-raw/1_1.cnt"

In [19]:
# Данная программа будет состоять из нескольких концептуальных частей:
# 1. feature_extraction/selection - выделяем только те данные, которые несут полезную информацию
# 2. principal component analysis
# 2. classification - классификация сигналов в соответствии с их свойствами,
# разнесение сигналов по соответствующим им эмоциям
# 3. visualisation - вставить красивую визуализацию
# Конечная цель - рабочая система, которая будет по загруженным в неё данным определять человеческую эмоцию

## Утилитарные функции

In [20]:
def calc_wavelet_energy(data_set):
    # Входные параметры: 1 * N vector

    # Выходные параметры: Энергия вейвлета входного вектора, округляется до 3 знаков после запятой.

    wavelet_energy = np.nansum(np.log2(np.square(data_set)))

    return round(wavelet_energy, 3)

In [21]:
def calc_shannon_entropy(data_set):
    # Входные параметры: 1 * N vector

    # Выходные параметры: Энтропией вейвлета входного вектора, округляется до 3 знаков после запятой.

    probability = np.square(data_set)
    shannon_entropy = -np.nansum(probability * np.log2(probability))

    return round(shannon_entropy, 3)

## Реализация основных функций

In [22]:
def feature_extraction():
    participant_trial = []
    features_table = pd.DataFrame(columns=range(620))
    files = os.listdir("C:/Users/alash/Desktop/4 курс/Diplom/program/datasets/SEED_EEG/SEED_EEG/Preprocessed_EEG/")
    for file in files:
        mat_file = spio.loadmat(
            "C:/Users/alash/Desktop/4 курс/Diplom/program/datasets/SEED_EEG/SEED_EEG/Preprocessed_EEG/" + file)
        keys = [key for key, values in mat_file.items() if
                key != '__header__' and key != '__version__' and key != '__globals__']
        for data_file in keys:
            data_df = pd.DataFrame(mat_file[data_file])

            m = data_df.shape[0]
            n = data_df.shape[1]
            # Извлечение функций модуля
            entropy = []
            energy = []
            for channel in data_df.iterrows():  # Итерация по 62 каналам
                dwt_bands = []
                data = channel[1]
                int_ent = []
                int_eng = []
                for band in range(5):
                    (data, coeff_d) = pywt.dwt(data, "db6")
                    dwt_bands.append(coeff_d)

                for band in range(len(dwt_bands)):  # DWT_bands = 23504, 11755
                    int_ent.append(calc_shannon_entropy(dwt_bands[len(dwt_bands) - band - 1]))
                    int_eng.append(calc_wavelet_energy(dwt_bands[len(dwt_bands) - band - 1]))

                entropy.append(int_ent)
                energy.append(int_eng)

            unroll_entropy = []
            unroll_energy = []
            # Преобразование 2D-массива в 1D-вектор функций, а затем объединение двух одномерных массивов.
            for i in range(len(entropy)):
                for j in range(len(entropy[0])):
                    unroll_entropy.append(entropy[i][j])
                    unroll_energy.append(energy[i][j])

            features = unroll_entropy + unroll_energy
            participant_trial.append(features)
            features_table.loc[len(features_table.index)] = features
            print(data_file)
            print(features)
        print(file)

    features_table.to_csv(directory + "features" + "db6" + ".csv", index=False)

In [23]:
feature_extraction()

ww_eeg1
[-40526712.624, -15847783.192, -5314878.757, -6269466.524, -8770646.48, -36789469.882, -14228330.859, -3533268.574, -2506881.784, -2809430.684, -32794268.403, -13792854.79, -7769986.727, -10929398.612, -14321953.021, -11763791.51, -6294415.746, -2800407.263, -2372966.325, -2035491.733, -12732586.028, -6935964.88, -4701384.496, -5351344.985, -4416647.967, -13975564.614, -8289169.267, -4369723.76, -4660774.149, -8237538.366, -6703144.997, -4602170.683, -2424367.667, -2074381.22, -2532975.458, -4905510.101, -3336650.405, -1635106.377, -1106135.058, -1252298.671, -4469047.842, -3088433.084, -1318205.058, -736044.003, -854019.645, -4420128.155, -3174148.256, -1350949.719, -719554.116, -950390.715, -4681604.867, -3202807.253, -1671726.307, -1126325.451, -1227405.96, -4901398.142, -3546797.307, -2719660.621, -2805108.002, -3017403.665, -8393490.078, -5929948.78, -6364373.887, -9759078.481, -13402593.615, -12127358.943, -7597575.065, -7219275.668, -10197711.303, -14824932.186, -1011213

ww_eeg3
[-69887335.564, -27731557.954, -6505416.893, -7679911.788, -8879474.364, -65512952.584, -25439561.518, -4516780.438, -3681902.497, -4068884.131, -60041933.557, -24066964.9, -7637031.202, -10948516.664, -12573569.749, -16994868.196, -8398164.902, -2574431.171, -1871207.823, -1390587.99, -42283598.038, -45993727.822, -56595014.194, -76162315.404, -206451379.355, -39724372.882, -25793803.66, -23150649.294, -28735372.009, -55510060.883, -11500453.641, -14984027.484, -24158370.226, -45526956.85, -158490717.32, -9184338.361, -6197777.387, -4655583.213, -5397168.823, -13416081.873, -4944141.362, -3110728.125, -1104976.8, -577607.715, -485602.121, -4790674.413, -3171931.701, -1179354.182, -607671.077, -575545.308, -5268473.398, -3229996.842, -1311828.338, -822191.909, -642773.99, -5578191.14, -3718454.708, -1852825.706, -1457391.047, -1134702.236, -8684640.565, -5819458.406, -3079736.583, -2908727.512, -2724305.516, -11304822.106, -6903981.951, -3121385.393, -2333814.952, -2593521.001,

ww_eeg5
[-27842470.485, -10576106.273, -4925881.876, -9186539.687, -9636236.089, -26131755.313, -9313476.327, -2793757.925, -3957022.571, -4023117.275, -23979726.066, -9443586.155, -6615798.506, -14246131.308, -15363982.627, -7975152.698, -4570531.486, -2052315.199, -2273036.375, -1621076.726, -9335592.84, -5916761.09, -5107479.454, -8724076.313, -9277924.477, -44885715.4, -42240119.461, -53786950.952, -80336773.229, -192638331.402, -4694215.376, -3297641.648, -1962501.149, -1647410.881, -1918863.61, -3314967.207, -2614102.919, -1184853.435, -804793.866, -683941.648, -3169079.409, -2575358.042, -1050044.315, -612201.049, -516863.671, -3227812.426, -2630029.751, -1066189.9, -640065.698, -611601.786, -3097515.711, -2402019.825, -1254700.856, -1012197.518, -780845.71, -3329444.217, -2559882.645, -1880229.338, -2050915.175, -1600054.266, -6079903.031, -3946361.464, -3342288.025, -4081938.415, -3554419.002, -8872592.818, -4796299.279, -2681808.758, -2154689.025, -2451178.293, -7703252.528, 

ww_eeg7
[-29255037.087, -13743061.141, -6474982.109, -12915818.158, -14922062.588, -28299806.91, -12837860.263, -3584487.884, -6134194.064, -6433451.781, -27002194.445, -12642849.177, -8070348.168, -16984955.784, -19156577.239, -9306101.397, -5381687.788, -2463468.14, -2617105.823, -2156173.767, -11249022.048, -6752406.863, -4803843.131, -7235079.689, -5400962.437, -38876641.115, -45145464.699, -70571655.499, -133145922.871, -366959879.316, -15906266.054, -24043630.757, -50925744.07, -105137537.03, -287037935.79, -4140363.211, -2838636.655, -1313772.662, -917440.365, -923154.268, -4005098.209, -2674653.064, -1128583.724, -722977.783, -723680.126, -3927379.314, -2673626.058, -1143800.125, -734879.254, -835132.815, -3999904.718, -2694557.313, -1398088.136, -1122516.505, -1053726.566, -4156946.529, -2995080.52, -2031985.583, -2213869.325, -2276044.896, -7333182.662, -4910857.166, -3978800.443, -5562410.673, -9421059.261, -10189502.852, -6203037.434, -3502676.211, -3258326.943, -4688948.12

ww_eeg9
[-39174742.741, -15483460.067, -5357981.97, -6024785.778, -8324185.231, -38641375.712, -15073357.117, -3689421.652, -2607803.832, -2644337.26, -36425509.879, -15564401.837, -6936665.021, -9701038.283, -11592107.234, -11682198.753, -6401643.014, -2818738.204, -2227989.119, -1852124.919, -13802211.862, -7912119.371, -4738851.301, -5459703.611, -4374779.407, -44405601.932, -84953006.151, -77654716.467, -140724841.978, -435342097.776, -44399649.39, -67908997.915, -128352652.826, -348393399.632, -1132126571.492, -5026093.092, -3488849.056, -1699649.406, -1083233.657, -1200518.34, -4731274.68, -3312906.058, -1392683.565, -744484.383, -762420.817, -4867790.55, -3333758.889, -1341247.476, -707310.669, -858608.541, -5017100.469, -3389665.215, -1610192.091, -1053936.482, -1075103.99, -5176521.613, -3743443.736, -2428471.676, -2373155.384, -2479986.639, -9662905.226, -6374371.302, -5327568.578, -7488026.528, -9029426.297, -15401274.043, -8783500.413, -6094293.891, -9132521.858, -13272252.

...

wk_eeg3
[-24757436.572, -5003191.814, -1244698.407, -963058.039, -1463691.574, -21449015.458, -4324549.369, -998266.036, -700739.792, -1053578.872, -22540035.285, -4511282.236, -1528923.829, -1642572.62, -2840133.426, -9462266.757, -2176069.395, -796652.354, -559662.275, -943365.008, -8833898.665, -2342064.131, -834468.849, -576385.957, -845197.21, -13717301.0, -3550271.684, -1523199.387, -1340259.062, -2203772.625, -6999414.534, -1910594.546, -725843.972, -443775.051, -795109.434, -6315077.056, -1745614.033, -671905.775, -385176.632, -624586.317, -2447168.623, -831138.462, -358101.744, -139196.943, -287656.642, -2295674.696, -867584.833, -374821.566, -142945.445, -263686.286, -2074481.507, -750374.547, -320808.523, -138048.061, -309262.179, -2023277.597, -740535.542, -328002.115, -184107.193, -516925.684, -3228870.588, -1247092.077, -592122.422, -468615.611, -923073.14, -4869425.702, -1828102.63, -914900.156, -913448.674, -1562279.961, -5356140.522, -2033953.808, -1072220.034, -945317

wk_eeg6
[-30969554.462, -4753453.906, -1989516.733, -2893717.053, -5347663.393, -24427952.899, -3802179.001, -1525301.124, -2219532.073, -3960087.986, -23728612.503, -3766329.215, -2637062.39, -4815514.15, -9599617.929, -12130350.527, -2290070.394, -1155403.848, -1559155.332, -3011103.564, -9322596.189, -2135105.233, -1238708.862, -1587118.437, -2346728.763, -17836053.773, -3872811.301, -2040167.9, -2637149.528, -4145380.436, -9424636.016, -2222562.864, -1011675.958, -1305082.54, -2100312.186, -8451822.869, -2016414.608, -911832.55, -1139216.176, -1731130.654, -3018310.011, -837219.901, -387591.621, -282843.365, -538302.746, -2542126.244, -810475.935, -364497.519, -195575.418, -368859.675, -2203754.555, -708578.371, -373751.254, -285970.422, -608796.272, -1984141.182, -708357.413, -602612.167, -768979.294, -1668732.648, -3100341.131, -1223828.835, -1564384.002, -2446820.739, -3889780.764, -4464119.436, -1876103.4, -3015189.102, -5241817.022, -8127995.472, -6651016.474, -2418453.981, -2

wk_eeg9
[-29344362.322, -7156978.583, -2226200.491, -2098038.184, -3793787.254, -23447632.892, -5861936.534, -2043065.977, -2012884.97, -3597124.412, -23806708.911, -5968814.26, -3173581.004, -4836414.726, -9205949.063, -11501251.139, -3953309.062, -1832893.786, -2555995.211, -5428192.992, -10192415.175, -3746149.633, -2345583.391, -3613534.685, -7716456.967, -19570636.461, -7546997.045, -10081969.619, -23938731.799, -48857858.779, -9504162.654, -3875332.113, -2429356.318, -5431650.156, -12238853.271, -8496014.759, -3650561.657, -2217402.653, -4529824.742, -10939574.619, -3100586.436, -2032167.419, -1728547.491, -3126994.371, -6218392.801, -2650659.681, -1705394.377, -920045.006, -792837.584, -1669102.103, -2496223.113, -1538052.184, -1318488.367, -1746151.723, -3623405.772, -2537573.989, -1719585.732, -2709914.128, -5459270.772, -10868545.545, -4318334.805, -2318382.606, -5753808.086, -8390923.25, -15918716.248, -6957825.716, -3490303.176, -7845115.732, -12636023.895, -26790113.523, -

wk_eeg11
[-19351507.54, -15026975.842, -2853263.878, -1039824.724, -1313957.663, -15764257.684, -14364947.774, -2505630.235, -610709.215, -787142.742, -15997405.032, -13921564.731, -2714826.578, -1072629.144, -1622167.464, -7838267.247, -11398357.669, -2222742.354, -779957.597, -1140861.785, -6535301.783, -10873386.878, -2099683.564, -581726.067, -801287.604, -14004562.697, -12550314.359, -2825566.469, -1203191.056, -2025906.807, -6830914.013, -9588242.203, -1885321.073, -516932.767, -855580.228, -6076436.645, -9153948.003, -1773433.94, -448137.212, -672581.41, -2095137.43, -7065000.348, -1214194.296, -191014.83, -351130.92, -1802214.894, -7733211.987, -1324346.354, -201127.679, -328054.245, -1634247.496, -6561816.675, -1147257.507, -189611.084, -389337.033, -1640970.033, -5514675.742, -1084172.912, -254735.495, -686087.559, -2755932.134, -6511016.185, -1499746.951, -619703.207, -1170752.891, -4619338.852, -8032273.376, -1998527.478, -918624.429, -1734008.112, -5695562.616, -8756834.10

wk_eeg13
[-32479299.755, -11556542.205, -3194749.885, -3014315.337, -4718571.835, -26661915.49, -10285644.853, -2012350.399, -1108018.715, -1762068.932, -26531963.442, -9763683.163, -2671238.071, -2698459.397, -4567023.544, -12831422.563, -7451114.544, -2188777.003, -1772417.694, -3574932.155, -10262715.195, -6867986.601, -2068481.84, -1969153.383, -3307233.233, -20292204.702, -9718437.613, -6709227.581, -11435580.446, -27228551.976, -10663365.882, -6816088.415, -2365881.467, -2767227.692, -7465792.559, -9417222.581, -6365856.98, -2085980.086, -2047540.179, -5587162.242, -3042516.015, -4077382.876, -1120075.159, -922010.846, -2006191.277, -2458364.932, -4143479.592, -945950.497, -356751.187, -654904.56, -2299972.01, -3592583.637, -984175.653, -777596.066, -1482276.95, -2172911.563, -3175792.888, -1482641.635, -2320519.711, -6111464.077, -3301573.568, -3748030.223, -2915109.924, -4011871.245, -10061863.317, -4995790.532, -4957417.743, -2932930.516, -3810322.977, -8767754.516, -7274032.0

In [24]:
def principal_component_analysis():
    data = pd.read_csv(directory + "features" + "db6" + ".csv")

    # 1. Нормализация данных и транспонирование
    normalised = pd.DataFrame(normalize(data, axis=0))

    # 2. Нахождение ковариационной матрицы
    covariance_df = normalised.cov()

    # 3. Собственные векторы
    u, s, v = np.linalg.svd(covariance_df)

    # 4. Основные компоненты
    data_reduced = normalised @ u
    data_reduced.head()

    data_reduced.to_csv(directory + "pc" + "db6" + ".csv", index=False)

In [ ]:
principal_component_analysis()

In [ ]:
def svm_classification():
    # Чтение данных и разделение
    pcs = pd.read_csv(directory + "pc" + "db6" + ".csv")

    outputs = pd.read_csv(directory + "outputs_main.csv", header=None)

    x = pcs.iloc[:, :].values
    y = outputs.iloc[:, :].values

    x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state=42)

    # Создание экземпляра модели
    svc = SVC()
    # Задание сетки параметров
    parameters_for_grid = {"C": (100, 1e3, 1e4, 1e5, 1e6, 1e7, 1e8, 1e9), "gamma": (1e-08, 1e-7, 1e-6, 1e-5)}
    # Создание объекта GridSearchCV
    grid_search = GridSearchCV(svc, parameters_for_grid, n_jobs=-1, cv=5)
    # Сопоставление объекта GridSearchCV с данными
    grid_search.fit(x_train, y_train)

    # Получение лучших параметров
    print(grid_search.best_params_)
    # Использования лучшей модели для прогноза
    svc_best = grid_search.best_estimator_
    # Получение лучшего результата
    accuracy = svc_best.score(x_test, y_test)
    print("Accuracy on the testing set is: {0:.1f}%".format(accuracy * 100))
    prediction = svc_best.predict(x_test)

    report = classification_report(y_test, prediction)
    print(accuracy)
    print(report)

In [ ]:
svm_classification()